In [1]:
#setup 3D box
%run -i program/billiard_defs.py
%run -i program/analysis.py

dim = 3
pw_collision_law = 'no_slip'
# pw_collision_law = 'specular'
sl = 10

# Create orthonormal basis (onb) for each of the 6 faces, basis vectors down columns, normal rightmost
# Dynamics depend only on the normal, but visualization needs the full onb
names = ['x_min','x_max','y_min','y_max','z_min','z_max']
onbs = []
v = np.array([1,0,0])
for d in range(3):
    for s in [1,-1]:
        onb = np.array([np.roll(v,i+d+1) for i in range(3)]).T
        onb[:,-1] *= s
        onbs.append(onb)        
        

# Create the 6 wall objects
wall = []
for (name, onb) in zip(names, onbs):
    wall.append(FlatWall(pos=-sl*onb[:,-1], basis=onb, name=name, collision_law=pw_collision_law, half_length=sl, half_width=sl))

bounding_box = np.array([[-sl,sl]
                         ,[-sl,sl]
                         ,[-sl,sl]
                        ])

lab_frame = np.eye(3)  #desired frame for lab

# Used for visualization later
surface_data_dict = []
for w in wall:
    w.parametrize()
    data_dict = {
        'name': w.name,
        'type': 'surface',
        'opacity': 0.4,
        'colorscale': [[0, 'rgb(0,0,255)'], [1, 'rgb(0,0,255)']],
        'showscale': False,
        'x': w.x,
        'y': w.y,
        'z': w.z
    }
    surface_data_dict.append(data_dict)

In [2]:
# Setup particles

num_part = 7
mass = 7
gamma = 'uniform'  #parameter btw 0 mass at center) and sqrt(2/dim) (mass on outside shell)
radius = 1
temp = 10
pp_collision_law = 'no_slip'
# pp_collision_law = 'specular'

In [4]:
%run -i program/billiard_defs.py
%run -i program/analysis.py

max_steps = 40
max_distort = 1000  # Used after experiment to determine whether to interpolate between collisions
# If so, how much distortion to allow.  Must be 0-100, smaller <-> more frames and smoother, but longer 
# processing and larger files.  Anything other than 0-100 will turn off smoothing

part = Particles(wall, num=num_part, mass=mass, gamma=gamma
                 ,radius=radius, temp=temp, collision_law=pp_collision_law
                 #,pos=init_pos  # comment this line out for random init pos
                 #, vel=init_vel  # comment this line out for random init vel
                )
init(wall, part)

for step in range(max_steps):
    do_the_evolution()

re_t, re_pos, re_vel, re_rot, re_spin = smoother(max_distort)
S, P, D, M = re_pos.shape

print("Finished it all.  There are {} frames in this animation of {} particles.".format(S, P))

Finished it all.  There are 41 frames in this animation of 7 particles.


In [5]:
interactive_3D()